In [26]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import geopandas as gpd
from sklearn.preprocessing import LabelEncoder
from cartoframes.viz import *

In [27]:
df1 = pd.read_csv('South Korea-seoul_Monthly_Match_2022-08-17.csv')             # Monthly
df2 = pd.read_csv('South Korea-seoul_Property_Extended_Match_2022-08-17.csv')   # property feature

/tmp/ipykernel_1339990/4235575856.py:1: DtypeWarning: Columns (24,27,28) have mixed types. Specify dtype option on import or set low_memory=False.
  df1 = pd.read_csv('South Korea-seoul_Monthly_Match_2022-08-17.csv')             # Monthly
/tmp/ipykernel_1339990/4235575856.py:2: DtypeWarning: Columns (26,51,59,60,62) have mixed types. Specify dtype option on import or set low_memory=False.
  df2 = pd.read_csv('South Korea-seoul_Property_Extended_Match_2022-08-17.csv')   # property feature


In [3]:
#df1.head()

In [4]:
#df2.head()

In [5]:
cols1 = df1.columns
cols2 = df2.columns

In [6]:
# 열별 데이터 분포 확인
cols1 = df1.columns
for col in cols1:
    print('=================================')
    print(f'<<{col}>>')
    print(f'unique number: {len(df1[col].unique())}')
    print(df1[col].value_counts())

<<Property ID>>
unique number: 77798
Property ID
ab-1237444               93
ab-4746708               93
ab-2912128               93
ab-1171492               93
ab-2939620               93
                         ..
ab-674947709111428190     1
ab-674896433968008509     1
ab-674836597266937180     1
ab-674779831380181937     1
ab-676712795371929759     1
Name: count, Length: 77798, dtype: int64
<<Property Type>>
unique number: 144
Property Type
Apartment                     571030
House                         281576
Rental unit                   276120
Home                          173913
Condominium                    85254
                               ...  
Private room in tiny house        12
Car                               11
Shared room in guest suite        10
Entire pension                    10
Train                              3
Name: count, Length: 143, dtype: int64
<<Listing Type>>
unique number: 5
Listing Type
Entire home/apt    1168341
Private room        703649
Shar

ADR (Native)
50000.00     6272
30000.00     5595
25000.00     5567
40000.00     4945
60000.00     4887
             ... 
89789.81        1
71257.43        1
112372.66       1
93707.55        1
60782.52        1
Name: count, Length: 362943, dtype: int64
<<Number of Reservations>>
unique number: 33
Number of Reservations
0.0     1243513
1.0      166624
2.0      115079
3.0       92434
4.0       82441
5.0       75455
6.0       64803
7.0       52566
8.0       39419
9.0       28829
10.0      20759
11.0      14466
12.0      10325
13.0       7550
14.0       5513
15.0       4117
16.0       3106
17.0       2393
18.0       1911
19.0       1506
20.0       1212
21.0        992
22.0        774
23.0        657
24.0        515
25.0        387
26.0        297
27.0        218
28.0        151
29.0         78
30.0         25
31.0          7
Name: count, dtype: int64
<<Reservation Days>>
unique number: 33
Reservation Days
0.0     1219780
1.0       56239
2.0       43622
3.0       36724
4.0       33664
5.0  

In [7]:
cols2 = df2.columns
for col in cols2:
    print('=================================')
    print(f'<<{col}>>')
    print(f'unique number: {len(df2[col].unique())}')
    print(df2[col].value_counts())

<<Property ID>>
unique number: 78426
Property ID
ab-35108       1
ab-26017161    1
ab-26020129    1
ab-26019975    1
ab-26019269    1
              ..
ab-16279750    1
ab-16279728    1
ab-16279692    1
ab-16279617    1
ha-987448      1
Name: count, Length: 78426, dtype: int64
<<Listing Title>>
unique number: 73337
Listing Title
Guest House                                           215
Apartment                                              83
Private APT near SNU/Ur home in the heart of Seoul     37
# 2 min walk from Sinseol-dong Station                 32
홍대3분 저렴 깔끔 조용                                          25
                                                     ... 
Cozy House(편안하고 안락한 집)                                  1
JAMES HOUSE_12PAX, 2BR, 2BA                             1
Cozy studio in Seoul                                    1
!Open Sale!! Super price!! Great location flat 2        1
near Hongik univ, Sinchon, Jongno Jun's APT             1
Name: count, Length: 73336, dtyp

# 서울시 구, 동 정보

In [8]:
dong_boundary = gpd.read_file('../emd2/행정구역.shp', encoding='CP949')
dong = dong_boundary[dong_boundary['ADM_CD'].str.startswith('11')]

dong['ADM_CD'] = dong['ADM_CD'].astype(str)

# 중복이름 동 방지
dong.loc[(dong['ADM_NM']=='신사동') & (dong['ADM_CD']=='1121068'), 'ADM_NM'] = '신사동(강남)'
dong.loc[(dong['ADM_NM']=='신사동') & (dong['ADM_CD']=='1123051'), 'ADM_NM'] = '신사동(관악)'

# CRS 변환
dong.set_crs(epsg=5179, inplace=True)
dong.to_crs(epsg=4326, inplace=True)

dong.shape

(424, 7)

In [9]:
dong.head()

SIDO_CD SIDO_NM SIGUNGU_CD SIGUNGU_NM   ADM_CD ADM_NM  \
0      11   서울특별시      11010        종로구  1101053    사직동   
1      11   서울특별시      11010        종로구  1101054    삼청동   
2      11   서울특별시      11010        종로구  1101055    부암동   
3      11   서울특별시      11010        종로구  1101056    평창동   
4      11   서울특별시      11010        종로구  1101057    무악동   

                                            geometry  
0  POLYGON ((126.97399 37.57823, 126.97400 37.578...  
1  POLYGON ((126.97714 37.59768, 126.97730 37.597...  
2  POLYGON ((126.96253 37.60575, 126.96246 37.605...  
3  POLYGON ((126.97508 37.63118, 126.97468 37.629...  
4  POLYGON ((126.96079 37.57378, 126.96074 37.573...

In [10]:
# 동 그래프 확인
dong_layer = Layer(dong,
                    basic_style(opacity=0.2), # 투명도
                    popup_hover=popup_element('ADM_NM', title='Region')) # 얹으면 팝업

In [11]:
df1_properties = df1['Property ID'].unique()
df2_properties = df2['Property ID'].unique()

print(df1.shape)
print(df2.shape)

# 교집합 계산
common_properties = np.intersect1d(df1_properties, df2_properties)
print(len(common_properties))   # df1이 df2에 존속됨

print(len(df1_properties))
print(len(df2_properties))

(2038365, 29)
(78426, 70)
77798
77798
78426


In [12]:
# geopandas dataframe 변환
coordinate1 = gpd.points_from_xy(df1['Longitude'], df1['Latitude'])
gdf = gpd.GeoDataFrame(df1, geometry=coordinate1)

# 좌표계 설정
gdf.set_crs(epsg=4326, inplace=True)

# 공간 조인을 사용하여 각 숙소의 위치가 어떤 동에 속하는지 확인
gdf = gpd.sjoin(gdf, dong[['geometry', 'ADM_NM']], how="left", op="within")

# 두 데이터 프레임(df1, df2) 결합(최종 데이터프레임)
gdf = gdf.merge(df2, on='Property ID', how='left', suffixes=('_gdf1', ''))

gdf.shape

/home/hj/anaconda3/envs/HJ/lib/python3.10/site-packages/IPython/core/interactiveshell.py:3517: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if await self.run_code(code, result, async_=asy):


(2038365, 101)

In [13]:
# df1, df2에서 동일한 이름으로 사용된 열 찾기
gdf1_columns = [col for col in gdf.columns if '_gdf1' in col]

print(gdf1_columns)
gdf = gdf.drop(columns=gdf1_columns)    # 중복되는 열은 df2를 기준으로 설정

gdf.shape

['Property Type_gdf1', 'Listing Type_gdf1', 'Bedrooms_gdf1', 'Country_gdf1', 'State_gdf1', 'City_gdf1', 'Zipcode_gdf1', 'Neighborhood_gdf1', 'Metropolitan Statistical Area_gdf1', 'Latitude_gdf1', 'Longitude_gdf1', 'Currency Native_gdf1', 'Airbnb Property ID_gdf1', 'Airbnb Host ID_gdf1', 'HomeAway Property ID_gdf1']


(2038365, 86)

In [14]:
# 서울 안에 있는 부동산만 이용
null_gdf = gdf[gdf['ADM_NM'].isnull()]
print(null_gdf['Property ID'].unique())
print(null_gdf.shape)

# 위치 확인
outlayer = Layer(null_gdf, popup_hover=popup_element('Property ID', title='Property ID'))

Map([dong_layer, outlayer])

['ab-49469791' 'ab-5948325' 'ab-13930279' 'ab-14749201' 'ab-18828514'
 'ab-42956695' 'ab-31111724']
(275, 86)


In [15]:
# 몇개 없으니까 직접 채우기
dong_dict = {'ab-49469791': '개봉3동', 
'ab-5948325': '강일동',
'ab-13930279': '독산1동',
'ab-14749201': '오류2동',
'ab-18828514': '시흥3동',
'ab-42956695': '수궁동',
'ab-31111724': '진관동'}

# 동 이름 채우기
for key, val in dong_dict.items():
    gdf.loc[gdf['Property ID']==key, 'ADM_NM'] = val

In [16]:
# 월, 동별 그룹핑
grouped = gdf.groupby(['Reporting Month', 'ADM_NM'])

# 각 달, 동 값 받아오기
mon = gdf['Reporting Month'].unique()
dong_name = gdf['ADM_NM'].unique()

In [17]:
# 그룹 데이터 불러오기
# print(mon[0], dong_name[0])
# grouped.get_group((mon[0], dong_name[0]))

In [18]:

core_features = ['Reporting Month', 'ADM_NM', 'Reservation Days', 'Available Days', 'Blocked Days', 'Property Type', 'Listing Type', 'Neighborhood', 'Currency Native', 'Number of Reviews', 'Bedrooms', 'Bathrooms', 
                 'Max Guests', 'Response Rate', 'Airbnb Response Time (Text)', 'Airbnb Superhost', 'Cancellation Policy', 'Security Deposit (USD)', 'Cleaning Fee (USD)', 
                 'Extra People Fee (USD)', 'Published Nightly Rate (USD)', 'Published Monthly Rate (USD)', 'Published Weekly Rate (USD)', 'Check-in Time', 'Checkout Time', 'Minimum Stay', 
                 'Number of Photos', 'Instantbook Enabled', 'Latitude', 'Longitude',  'Pets Allowed', 'Integrated Property Manager']  # 'Amenities' 너무 많아서 제거

print(len(core_features))
raw_embeddings = gdf[core_features]


# core_features 리스트가 이미 정의되어 있다고 가정
# raw_embeddings 데이터프레임 준비
raw_embeddings = gdf[core_features].copy()  # 원본 보호를 위해 복사

raw_embeddings['Reporting Month'] = pd.to_datetime(raw_embeddings['Reporting Month'])

# 2017년 1월 1일 이후의 데이터만 필터링
raw_embeddings = raw_embeddings[raw_embeddings['Reporting Month'] >= '2017-01-01']
raw_embeddings

32


Reporting Month ADM_NM  Reservation Days  Available Days  \
0            2022-06-01    혜화동               1.0            29.0   
1            2022-07-01    혜화동              10.0            15.0   
2            2022-06-01    사근동               0.0            30.0   
3            2022-07-01    사근동               0.0            31.0   
4            2022-07-01    연남동              24.0             7.0   
...                 ...    ...               ...             ...   
2038360      2021-03-01    역촌동               0.0            31.0   
2038361      2021-04-01    역촌동               0.0            30.0   
2038362      2021-05-01    역촌동               0.0            31.0   
2038363      2021-06-01    역촌동               0.0            30.0   
2038364      2021-07-01    역촌동               0.0             0.0   

         Blocked Days Property Type     Listing Type  Neighborhood  \
0                 0.0   Rental unit     Private room   Seongbuk-gu   
1                 6.0   Rental unit     Private room   Seongbuk-gu   
2                 0.0   Rental unit  Entire home/apt  Seongdong-gu   
3                 0.0   Rental unit  Entire home/apt  Seongdong-gu   
4                 0.0     Townhouse     Private room       Mapo-gu   
...               ...           ...              ...           ...   
2038360           0.0     Apartment  Entire home/apt  Eunpyeong-gu   
2038361           0.0     Apartment  Entire home/apt  Eunpyeong-gu   
2038362           0.0     Apartment  Entire home/apt  Eunpyeong-gu   
2038363           0.0     Apartment  Entire home/apt  Eunpyeong-gu   
2038364           0.0     Apartment  Entire home/apt  Eunpyeong-gu   

        Currency Native  Number of Reviews  ...  Published Weekly Rate (USD)  \
0                   KRW                0.0  ...                          NaN   
1                   KRW                0.0  ...                          NaN   
2                   USD                0.0  ...                          NaN   
3                   USD                0.0  ...                          NaN   
4                   KRW                0.0  ...                          NaN   
...                 ...                ...  ...                          ...   
2038360             NaN                1.0  ...                          NaN   
2038361             NaN                1.0  ...                          NaN   
2038362             NaN                1.0  ...                          NaN   
2038363             NaN                1.0  ...                          NaN   
2038364             NaN                1.0  ...                          NaN   

         Check-in Time  Checkout Time  Minimum Stay Number of Photos  \
0        After 3:00 PM       11:00 AM           1.0             20.0   
1        After 3:00 PM       11:00 AM           1.0             20.0   
2        After 3:00 PM       11:00 AM         200.0             11.0   
3        After 3:00 PM       11:00 AM         200.0             11.0   
4        After 3:00 PM       11:00 AM           3.0             15.0   
...                ...            ...           ...              ...   
2038360            NaN            NaN           3.0             17.0   
2038361            NaN            NaN           3.0             17.0   
2038362            NaN            NaN           3.0             17.0   
2038363            NaN            NaN           3.0             17.0   
2038364            NaN            NaN           3.0             17.0   

        Instantbook Enabled   Latitude   Longitude  Pets Allowed  \
0                     False  37.588926  126.992914         False   
1                     False  37.588926  126.992914         False   
2                     False  37.557404  127.040654         False   
3                     False  37.557404  127.040654         False   
4                     False  37.560640  126.918663         False   
...                     ...        ...         ...           ...   
2038360                True  37.603220  126.9146

In [19]:
# 범주형 변수 확인
cat_list = raw_embeddings.select_dtypes(include=['object', 'category']).columns
num = 0
for col in cat_list:
    if col == 'ADM_NM':
        continue
    print(col)
    #print(raw_embeddings[col].unique())
    print(len(raw_embeddings[col].unique()))
    num += len(raw_embeddings[col].unique())
print(f'total: {num}')

Property Type
142
Listing Type
5
Neighborhood
26
Currency Native
21
Airbnb Response Time (Text)
5
Airbnb Superhost
3
Cancellation Policy
44
Check-in Time
392
Checkout Time
51
Pets Allowed
3
Integrated Property Manager
3
total: 695


In [20]:
# 제외할 열을 제외한 나머지 열을 one-hot 인코딩
numeric_columns = raw_embeddings.select_dtypes(include=['number']).columns
excluded_columns = ['Reporting Month', 'ADM_NM']
excluded_columns.extend(numeric_columns)

encoded_df = pd.get_dummies(raw_embeddings.drop(columns=excluded_columns), drop_first=True)

# 제외한 열을 다시 추가
raw_embeddings = pd.concat([raw_embeddings[excluded_columns], encoded_df], axis=1)

raw_embeddings

Reporting Month ADM_NM  Reservation Days  Available Days  \
0            2022-06-01    혜화동               1.0            29.0   
1            2022-07-01    혜화동              10.0            15.0   
2            2022-06-01    사근동               0.0            30.0   
3            2022-07-01    사근동               0.0            31.0   
4            2022-07-01    연남동              24.0             7.0   
...                 ...    ...               ...             ...   
2038360      2021-03-01    역촌동               0.0            31.0   
2038361      2021-04-01    역촌동               0.0            30.0   
2038362      2021-05-01    역촌동               0.0            31.0   
2038363      2021-06-01    역촌동               0.0            30.0   
2038364      2021-07-01    역촌동               0.0             0.0   

         Blocked Days  Number of Reviews  Bedrooms  Bathrooms  Max Guests  \
0                 0.0                0.0       1.0        0.0         1.0   
1                 6.0                0.0       1.0        0.0         1.0   
2                 0.0                0.0       1.0        1.0         2.0   
3                 0.0                0.0       1.0        1.0         2.0   
4                 0.0                0.0       1.0        1.0         3.0   
...               ...                ...       ...        ...         ...   
2038360           0.0                1.0       1.0        1.0         4.0   
2038361           0.0                1.0       1.0        1.0         4.0   
2038362           0.0                1.0       1.0        1.0         4.0   
2038363           0.0                1.0       1.0        1.0         4.0   
2038364           0.0                1.0       1.0        1.0         4.0   

         Response Rate  ...  Checkout Time_8:00 AM  Checkout Time_8:00 PM  \
0                 95.0  ...                  False                  False   
1                 95.0  ...                  False                  False   
2                100.0  ...                  False                  False   
3                100.0  ...                  False                  False   
4                  NaN  ...                  False                  False   
...                ...  ...                    ...                    ...   
2038360           83.0  ...                  False                  False   
2038361           83.0  ...                  False                  False   
2038362           83.0  ...                  False                  False   
2038363           83.0  ...                  False                  False   
2038364           83.0  ...                  False                  False   

         Checkout Time_8AM  Checkout Time_8PM  Checkout Time_9:00 AM  \
0                    False              False                  False   
1                    False              False                  False   
2                    False              False                  False   
3                    False              False                  False   
4                    False              False                  False   
...                    ...                ...                    ...   
2038360              False              False                  False   
2038361              False              False                  False   
2038362              False              False                  False   
2038363              False              False                  False   
2038364              False              False                  False   

         Checkout Time_9:00 PM  Checkout Time_9AM  Checkout Time_9PM  \
0                        False              False              False   
1                        False              False              False   
2                        False              False              False   
3                        False              False              False   
4                        False              False              False   
...                        ...              

In [21]:
# 빈 부분 채우기
grouped = raw_embeddings.groupby(['Reporting Month', 'ADM_NM']).mean().reset_index()

date_range = pd.date_range(start='2017-01-01', end='2022-07-01', freq='MS')
print(len(date_range))

# 동 이름과 날짜 범위의 모든 조합 생성
dong_name
print(len(dong_name))

full_index = pd.MultiIndex.from_product([dong_name, date_range], names=['ADM_NM', 'Reporting Month'])
#full_index

existing_index = pd.MultiIndex.from_frame(grouped[['ADM_NM', 'Reporting Month']])

# 존재하지 않는 조합 찾기
missing_combinations = set(full_index) - set(existing_index)

print(len(missing_combinations))

# 기존 데이터프레임에서 인덱스 생성
existing_index = pd.MultiIndex.from_frame(grouped[['ADM_NM', 'Reporting Month']])

missing_combinations_df = pd.DataFrame(
    list(missing_combinations), 
    columns=['ADM_NM', 'Reporting Month']
)

fills = grouped.columns[2:]
print(fills)

for c in fills:
    missing_combinations_df[c] = 0

raw_result = pd.concat([grouped, missing_combinations_df])

67
424
539
Index(['Reservation Days', 'Available Days', 'Blocked Days',
       'Number of Reviews', 'Bedrooms', 'Bathrooms', 'Max Guests',
       'Response Rate', 'Security Deposit (USD)', 'Cleaning Fee (USD)',
       ...
       'Checkout Time_8:00 AM', 'Checkout Time_8:00 PM', 'Checkout Time_8AM',
       'Checkout Time_8PM', 'Checkout Time_9:00 AM', 'Checkout Time_9:00 PM',
       'Checkout Time_9AM', 'Checkout Time_9PM', 'Pets Allowed_True',
       'Integrated Property Manager_True'],
      dtype='object', length=692)


/tmp/ipykernel_1339990/3063311412.py:33: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  missing_combinations_df[c] = 0
/tmp/ipykernel_1339990/3063311412.py:33: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  missing_combinations_df[c] = 0
/tmp/ipykernel_1339990/3063311412.py:33: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newfr

In [22]:
# 순서 맞추기
road = pd.read_csv('Raw_Embeddings/Road_Embeddings.csv')
adm_order = road['ADM_NM'].tolist()

final_raw_embedding = []

for day in date_range:
    now_df = raw_result.loc[raw_result['Reporting Month']==day]
    sort_df = now_df.set_index('ADM_NM').reindex(adm_order).reset_index()
    final_raw_embedding.append(sort_df)

# 최종 데이터프레임으로 결합
final_raw_embedding_df = pd.concat(final_raw_embedding, ignore_index=True)
final_raw_embedding_df = final_raw_embedding_df.fillna(0)   # 결측값 채우기
final_raw_embedding_df


ADM_NM Reporting Month  Reservation Days  Available Days  \
0              사직동      2017-01-01          5.251938       21.348837   
1              삼청동      2017-01-01          3.473684       23.168421   
2              부암동      2017-01-01          3.000000       25.121212   
3              평창동      2017-01-01          0.877551       27.653061   
4              한남동      2017-01-01          5.700508       20.218274   
...            ...             ...               ...             ...   
28403          가회동      2022-07-01         10.133333        8.051852   
28404  종로1·2·3·4가동      2022-07-01          9.106501        8.633472   
28405         방배2동      2022-07-01          7.600000        9.133333   
28406          미아동      2022-07-01          6.600000        5.266667   
28407          인수동      2022-07-01          3.363636        7.545455   

       Blocked Days  Number of Reviews  Bedrooms  Bathrooms  Max Guests  \
0          4.399225          29.542636  1.250000   1.153101    4.205426   
1          4.357895          19.273684  1.178947   1.157609    3.568421   
2          2.878788          10.303030  1.242424   1.196970    2.621212   
3          2.469388           9.428571  1.428571   1.387755    4.367347   
4          5.081218          21.588832  1.467005   1.286082    3.593909   
...             ...                ...       ...        ...         ...   
28403     12.814815          44.629630  1.518519   1.481481    3.933333   
28404     13.260028          25.002766  0.988935   1.105809    2.526971   
28405     14.266667          15.000000  0.933333   1.066667    2.000000   
28406     19.133333          10.066667  1.133333   1.066667    2.266667   
28407     20.090909          50.454545  1.000000   1.000000    2.909091   

       Response Rate  ...  Checkout Time_8:00 AM  Checkout Time_8:00 PM  \
0          91.214286  ...                    0.0                    0.0   
1          66.404255  ...                    0.0                    0.0   
2          87.241935  ...                    0.0                    0.0   
3          74.523810  ...                    0.0                    0.0   
4          88.171429  ...                    0.0                    0.0   
...              ...  ...                    ...                    ...   
28403      87.552000  ...                    0.0                    0.0   
28404      93.623824  ...                    0.0                    0.0   
28405      92.076923  ...                    0.0                    0.0   
28406      67.909091  ...                    0.0                    0.0   
28407      99.200000  ...                    0.0                    0.0   

       Checkout Time_8AM  Checkout Time_8PM  Checkout Time_9:00 AM  \
0                    0.0           0.000000                    0.0   
1                    0.0           0.000000                    0.0   
2                    0.0           0.000000                    0.0   
3                    0.0           0.000000                    0.0   
4                    0.0           0.005076                    0.0   
...                  ...                ...                    ...   
28403                0.0           0.000000                    0.0   
28404                0.0           0.000000                    0.0   
28405                0.0           0.000000                    0.0   
28406                0.0           0.000000                    0.0   
28407                0.0           0.000000                    0.0   

       Checkout Time_9:00 PM  Checkout Time_9AM  Checkout Time_9PM  \
0                        0.0           0.003876                0.0   
1                        0.0           0.000000                0.0   
2                        0.0           0.000000                0.0   
3                        0.0           0.000000                0.0   
4                        0.0           0.000000                0.0   
...                      ...                ...                ...   
28403         

In [23]:
# 기본 임베딩 저장
final_raw_embedding_df.drop(columns=['ADM_NM', 'Reporting Month'], inplace=False).to_csv(
    'Raw_Embeddings/AirBnB_Embeddings.csv', 
    index=False, 
    header=False
)

# gnn 학습용 그래프 임베딩 확인
for_gnn_ver = final_raw_embedding_df.copy()
for_gnn_ver.to_csv('Raw_Embeddings/AirBnB_Embeddings_with_name_mon.csv', index=False)

In [24]:
dff = pd.read_csv('Raw_Embeddings/HumanFlow_Embeddings_code.csv')

raw_embeddings.shape, dff.shape

((1807822, 694), (28408, 37))

In [25]:
# 전처리 원본 저장
gdf.to_csv('preprocess_AirBnB.csv', index=False)